In [4]:
!pip install transformers datasets

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Using cached transformers-4.30.2-py3-none-any.whl (7.2 MB)
  Using cached datasets-2.13.1-py3-none-any.whl (486 kB)
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.8/236.8 kB 8.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 103.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.3/1.3 MB 83.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 110.5/110.5 kB 16.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 212.5/212.5 kB 27.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.3/134.3 kB 18.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 72.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 114.5/114.5 kB 17.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 268.8/268.8 kB 34.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 149.6/149.6 kB 

In [5]:
import tensorflow as tf

In [6]:
tf.config.set_visible_devices(tf.config.list_physical_devices('GPU'), 'GPU')

In [7]:
print("Num GPUs Available: ", len(tf.config.list_physical_devices('GPU')))

Num GPUs Available:  1


In [8]:
from datasets import load_dataset

dataset = load_dataset("fazni/roles-based-on-skills")

Extracting data files:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Dataset csv downloaded and prepared to /root/.cache/huggingface/datasets/fazni___csv/fazni--roles-based-on-skills-85f4f4efc5a3cc58/0.0.0/eea64c71ca8b46dd3f537ed218fc9bf495d5707789152eb2764f5c78fa66d59d. Subsequent calls will reuse this data.


  0%|          | 0/1 [00:00<?, ?it/s]

In [9]:
data = dataset['train']

In [10]:
y = data['Target']
X = data['ALL']

In [11]:
from sklearn.preprocessing import LabelEncoder
le = LabelEncoder()
label = le.fit_transform(y)
# Data_tokenized.drop("Target", axis=1, inplace=True)
label

array([9, 9, 9, ..., 3, 3, 3])

In [12]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, label, test_size=0.2, random_state=42)

In [13]:
# Importing pretrained model and it's tokenizer from HuggingFace
from transformers import DistilBertTokenizer, DistilBertForSequenceClassification

tokenizer = DistilBertTokenizer.from_pretrained("distilbert-base-uncased")

In [14]:
train_encoding = tokenizer(X_train,truncation=True,padding=True)
test_encoding = tokenizer(X_test,truncation=True,padding=True)

In [ ]:
train_encoding

## Converting Encodings into data Objects

In [16]:
import tensorflow as tf

train_dataset = tf.data.Dataset.from_tensor_slices((
    dict(train_encoding),
    y_train
))

test_dataset = tf.data.Dataset.from_tensor_slices((
    dict(test_encoding),
    y_test
))

In [17]:
train_dataset

<_TensorSliceDataset element_spec=({'input_ids': TensorSpec(shape=(357,), dtype=tf.int32, name=None), 'attention_mask': TensorSpec(shape=(357,), dtype=tf.int32, name=None)}, TensorSpec(shape=(), dtype=tf.int64, name=None))>

In [18]:
num_classes=10

In [19]:
from transformers import DistilBertConfig, TFDistilBertForSequenceClassification, TFTrainer, TFTrainingArguments

# Set up the model configuration
model_config = DistilBertConfig.from_pretrained("distilbert-base-uncased", num_labels=num_classes)

training_arguments = TFTrainingArguments(
    output_dir='/content/drive/MyDrive/HuggingFace/RoleBasedPrediction/results',
    num_train_epochs=2,
    per_device_train_batch_size=8,
    per_device_eval_batch_size=16,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='/content/drive/MyDrive/HuggingFace/RoleBasedPrediction/logs',
    logging_steps=10,
    eval_steps=500,
)

In [20]:
with training_arguments.strategy.scope():
  model = TFDistilBertForSequenceClassification.from_pretrained("distilbert-base-uncased", config=model_config)

trainer = TFTrainer(
    model=model,
    args=training_arguments,
    train_dataset=train_dataset,
    eval_dataset=test_dataset
)

trainer.train()

Some weights of the PyTorch model were not used when initializing the TF 2.0 model TFDistilBertForSequenceClassification: ['vocab_transform.weight', 'vocab_projector.bias', 'vocab_layer_norm.bias', 'vocab_layer_norm.weight', 'vocab_transform.bias']
- This IS expected if you are initializing TFDistilBertForSequenceClassification from a PyTorch model trained on another task or with another architecture (e.g. initializing a TFBertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing TFDistilBertForSequenceClassification from a PyTorch model that you expect to be exactly identical (e.g. initializing a TFBertForSequenceClassification model from a BertForSequenceClassification model).
Some weights or buffers of the TF 2.0 model TFDistilBertForSequenceClassification were not initialized from the PyTorch model and are newly initialized: ['pre_classifier.weight', 'pre_classifier.bias', 'classifier.weight', 'classifier.bias']
You should 

In [22]:
trainer.evaluate(test_dataset)

{'eval_loss': 0.10571072841512746}

In [ ]:
trainer.predict(test_dataset)

In [24]:
output=trainer.predict(test_dataset)[1]

In [25]:
from sklearn.metrics import confusion_matrix

cm = confusion_matrix(y_test,output)
cm

array([[103,   0,   0,   0,   0,   0,   0,   0,   0,   0],
       [  0,  77,   0,   0,   0,   0,   0,   0,   0,   0],
       [  0,   0,  52,   0,   0,   0,   0,   0,   0,   0],
       [  0,   0,   0,  86,   0,   0,   0,   0,   0,   0],
       [  0,   0,   0,   0,  90,   0,   0,   0,   0,   0],
       [  0,   0,   0,   0,   0,  87,   0,   0,   0,   0],
       [  0,   0,   0,   0,   0,   0,  76,   0,   0,   0],
       [  0,   0,   0,   0,   0,   0,   0, 100,   0,   0],
       [  0,   0,   0,   0,   0,   0,   0,   0,  99,   0],
       [  0,   0,   0,   0,   0,   0,   0,   0,   0, 146]])

In [23]:
trainer.save_model('/content/drive/MyDrive/HuggingFace/model')

In [ ]:
"Machine Learning,Deep Learning, Tensoflow, Python, Scikit Learn, Keras, Pandas and Numopy Libraries",

In [75]:
input_text = ["MySQL , html, javascript, Java, OOP, PHP,React, nodejs, Angular, npm, bootstrap, css, Springboot, Postman"]
inputs = tokenizer(input_text, truncation=True, padding=True, return_tensors="tf")
dummy_labels = [0] * len(input_text)

input_dataset = tf.data.Dataset.from_tensor_slices((
    dict(inputs),
    dummy_labels
))
result = trainer.predict(input_dataset)


In [51]:
outcome_labels = ['Business Analyst', 'Cyber Security','Data Engineer','Data Science','DevOps','Machine Learning Engineer','Mobile App Developer','Network Engineer','Quality Assurance','Software Engineer']

In [77]:
result

PredictionOutput(predictions=array([[-2.2625058 , -0.8229124 , -0.4219835 ,  0.89383066, -1.8038672 ,
         3.6242735 , -0.49239844, -2.4593642 , -2.3697128 ,  1.5308456 ]],
      dtype=float32), label_ids=array([0], dtype=int32), metrics={'eval_loss': 6.106631755828857})

In [76]:
result[0].argmax()

5

In [ ]:
predicted_class_id = logits.argmax().item()
model.config.id2label[predicted_class_id]